## ***Пояснения находятся в файле module-6.***

In [ ]:
#Для работы с данными
import numpy as np
import pandas as pd
#Для парсинга
import requests
from lxml import html
#Прочее
import json
import collections

# 1.Функции

In [2]:
def get_url_for_brand_on_page(page, brand, model):
    '''
    Получение списка url-адресов на машину по брэнду и модели.
    Вход:
    * page - номер страницы на auto.ru;
    * brand - марка машины;
    * model - модель машины.
    Выход:
    * Список url-адресов.
    '''
    #Формирование адреса
    url = 'https://auto.ru/cars/' + brand + '/' + model + '/used/?page=' + str(page)
    #Загрузка страницы поиска
    response = requests.get(url)
    tree = html.fromstring(response.content)
    #Сбор данных
    xpath_url = tree.xpath('//h3[@class="ListingItemTitle-module__container ListingItem-module__title"]/a/@href')
    #Вывод информации
    print('Страница {} по бренду {} по модели {} собрана.'.format(page,brand,model))
    return xpath_url

def get_date_for_url(url):
    '''
    Получение параметров машины по ее url-адресу.
    Вход:
    * url - url адрес страницы на auto.ru.
    Выход:
    * Параметры машины.
    '''
    #Загрузка страницы поиска
    response = requests.get(url)
    if response.status_code == 200:
        tree = html.fromstring(response.content)
        #Сбор данных
        xpath_year = tree.xpath('//li[@class="CardInfoRow CardInfoRow_year"]//text()')
        xpath_mileage = tree.xpath('//li[@class="CardInfoRow CardInfoRow_kmAge"]//text()')
        xpath_bodytype = tree.xpath('//li[@class="CardInfoRow CardInfoRow_bodytype"]//text()')
        xpath_color = tree.xpath('//li[@class="CardInfoRow CardInfoRow_color"]//text()')
        xpath_engine = tree.xpath('//li[@class="CardInfoRow CardInfoRow_engine"]//text()')
        xpath_transmission = tree.xpath('//li[@class="CardInfoRow CardInfoRow_transmission"]//text()')
        xpath_drive = tree.xpath('//li[@class="CardInfoRow CardInfoRow_drive"]//text()')
        xpath_wheel = tree.xpath('//li[@class="CardInfoRow CardInfoRow_wheel"]//text()')
        xpath_state = tree.xpath('//li[@class="CardInfoRow CardInfoRow_state"]//text()')
        xpath_ownersCount = tree.xpath('//li[@class="CardInfoRow CardInfoRow_ownersCount"]//text()')
        xpath_pts = tree.xpath('//li[@class="CardInfoRow CardInfoRow_pts"]//text()')
        xpath_customs = tree.xpath('//li[@class="CardInfoRow CardInfoRow_customs"]//text()')
        xpath_equipment = tree.xpath('//li[@class="ComplectationGroups__itemContentEl"]//text()')
        xpath_price = tree.xpath('//span[@class="OfferPriceCaption PriceUsedOffer-module__caption"]//text()')
    else:
        print('Пустая страница: {}'.format(url))
        xpath_year = '[]'
        xpath_mileage = '[]'
        xpath_bodytype = '[]'
        xpath_color = '[]'
        xpath_engine = '[]'
        xpath_transmission = '[]'
        xpath_drive = '[]'
        xpath_wheel = '[]'
        xpath_state = '[]'
        xpath_ownersCount = '[]'
        xpath_pts = '[]'
        xpath_customs = '[]'
        xpath_equipment = '[]'
        xpath_price = '[]'
    return pd.DataFrame({
        'url': [url],
        'year':[xpath_year],
        'mileage':[xpath_mileage],
        'type_body':[xpath_bodytype],
        'color':[xpath_color],
        'char_engine':[xpath_engine],
        'type_transmission':[xpath_transmission],
        'type_drive':[xpath_drive],
        'type_wheel':[xpath_wheel],
        'state':[xpath_state],
        'count_owners':[xpath_ownersCount],
        'pts':[xpath_pts],
        'customs':[xpath_customs],
        'equipment':[xpath_equipment],
        'price':[xpath_price]})

In [3]:
def parsing(dict_url,name):
    '''
    Функция для парсинга по имеющимся url.
    Вход:
    * dict_url - словарь с списками;
    * name - название папки.
    Выход:
    * None.
    '''
    #Информация о количестве url
    sum_all_url,sum_url = sum([len(dict_url[i][j]) for i in dict_url for j in dict_url[i]]),0
    #Сбор данных
    for brand in dict_url:
        for model in dict_url[brand]:
            #Извлечение
            list_url = dict_url[brand][model]
            df, len_urls = pd.DataFrame(), len(list_url)
            #Вывод информации
            print('Начало сбора данных по {}, {}. Всего url: {}. Всего собрано: {} / {}.'.\
                  format(brand,model,len_urls,sum_url,sum_all_url))
            #Сбор информации
            for i, url in enumerate(list_url):
                df_new = get_date_for_url(url)
                df = pd.concat([df,df_new])
                print('Собрано {} / {}.'.format(i+1,len_urls))
            #Вывод в csv файл
            sum_url += len_urls
            df.to_csv('Data/'+name+'_sub/'+brand+'_'+model+'_'+name+'.csv')
    pass

def union_data(dict_url,name):
    '''
    Функция для объединения данных при парсинге по имеющимся url.
    Вход:
    * dict_url - словарь с списками;
    * name - название папки.
    Выход:
    * None.
    '''
    df = pd.DataFrame()
    #Сбор в один файл
    for brand in dict_url:
        for model in dict_url[brand]:
            df_brand = pd.read_csv('Data/'+name+'_sub/'+brand+'_'+model+'_'+name+'.csv')
            df = pd.concat([df,df_brand])
    #Вывод в csv файл
    df.to_csv('Data/'+name+'.csv')
    pass

# 2.Чтение и анализ данных

In [4]:
#Чтение данных для тестовой выборки
df_test = pd.read_csv('Data/test_Kaggle.csv')

In [5]:
#Осмотр данных
df_test.iloc[0,:]

bodyType                                                          лифтбек
brand                                                               SKODA
car_url                 https://auto.ru/cars/used/sale/skoda/octavia/1...
color                                                               синий
complectation_dict                                                    NaN
description             Все автомобили, представленные в продаже, прох...
engineDisplacement                                                1.2 LTR
enginePower                                                       105 N12
equipment_dict          {"engine-proof":true,"tinted-glass":true,"airb...
fuelType                                                           бензин
image                   https://autoru.naydex.net/o9DBXQ270/5ac010hAY0...
mileage                                                             74000
modelDate                                                            2013
model_info              {"code":"OCTAV

In [6]:
#Список брендов
list_brand = [brand.lower() for brand in list(df_test['brand'].unique())]
list_brand

['skoda',
 'audi',
 'honda',
 'volvo',
 'bmw',
 'nissan',
 'infiniti',
 'mercedes',
 'toyota',
 'lexus',
 'volkswagen',
 'mitsubishi']

# 3.Парсинг данных train

In [48]:
#Максимальное число страниц
max_page = 100
#Создание словаря
dict_url = {}
#Число собранных данных
n_model = 0
n_brand = 0
n_all = 0
for brand in list_brand:
    #Создание словаря
    n_brand = 0
    dict_url_brand = {}
    #Список моделей
    list_model = list(df_test[df_test['brand'] == brand.upper()]['car_url'].apply(lambda x: x.split('/')[7]).unique())
    print('\nНачало бренда: {}. Количество моделей: {}. Список моделей: {}'.format(brand,len(list_model),list_model),end='\n'*2)
    for model in list_model:
        print('\nНачало модели: {}.'.format(model),end='\n'*2)
        n_model = 0
        list_url = []
        #Собираем
        for page in range(1,max_page):
            new_list = get_url_for_brand_on_page(page, brand, model)
            double_url = sum([x in list_url for x in new_list])
            #Для вывода информации
            n_model += len(new_list) - double_url
            n_brand += len(new_list) - double_url
            n_all += len(new_list) - double_url
            #Вывод информации
            print('Количество совпадение на странице {}: {}. Количество собранных данных: {}'.\
                  format(page,double_url,len(new_list)))
            print('Собрано всего данных: {}. Собрано данных по бренду: {}. Собрано данных по модели: {}'.\
                  format(n_all,n_brand,n_model))
            #Остановка, если все адреса повторы
            if double_url != len(new_list):
                list_url += new_list
            else:
                print('Прерывание.')
                break
        #Удаление повторений
        list_url = list(set(list_url))
        #Записываем
        dict_url_brand[model] = list_url
    #Записываем
    dict_url[brand] = dict_url_brand


Начало бренда: skoda. Количество моделей: 15. Список моделей: ['octavia', 'superb', 'octavia_rs', 'yeti', 'kodiaq', 'rapid', 'fabia', 'roomster', 'felicia', 'karoq', 'fabia_rs', '120', '100_series', 'favorit', 'popular']


Начало модели: octavia.

Страница 1 по бренду skoda по модели octavia собрана.
Количество совпадение на странице 1: 0. Количество собранных данных: 38
Собрано всего данных: 38. Собрано данных по бренду: 38. Собрано данных по модели: 38
Страница 2 по бренду skoda по модели octavia собрана.
Количество совпадение на странице 2: 0. Количество собранных данных: 38
Собрано всего данных: 76. Собрано данных по бренду: 76. Собрано данных по модели: 76
Страница 3 по бренду skoda по модели octavia собрана.
Количество совпадение на странице 3: 0. Количество собранных данных: 38
Собрано всего данных: 114. Собрано данных по бренду: 114. Собрано данных по модели: 114
Страница 4 по бренду skoda по модели octavia собрана.
Количество совпадение на странице 4: 0. Количество собранных 

Страница 38 по бренду skoda по модели octavia собрана.
Количество совпадение на странице 38: 0. Количество собранных данных: 37
Собрано всего данных: 1414. Собрано данных по бренду: 1414. Собрано данных по модели: 1414
Страница 39 по бренду skoda по модели octavia собрана.
Количество совпадение на странице 39: 0. Количество собранных данных: 37
Собрано всего данных: 1451. Собрано данных по бренду: 1451. Собрано данных по модели: 1451
Страница 40 по бренду skoda по модели octavia собрана.
Количество совпадение на странице 40: 1. Количество собранных данных: 37
Собрано всего данных: 1487. Собрано данных по бренду: 1487. Собрано данных по модели: 1487
Страница 41 по бренду skoda по модели octavia собрана.
Количество совпадение на странице 41: 0. Количество собранных данных: 37
Собрано всего данных: 1524. Собрано данных по бренду: 1524. Собрано данных по модели: 1524
Страница 42 по бренду skoda по модели octavia собрана.
Количество совпадение на странице 42: 0. Количество собранных данных:

Страница 76 по бренду skoda по модели octavia собрана.
Количество совпадение на странице 76: 0. Количество собранных данных: 37
Собрано всего данных: 2816. Собрано данных по бренду: 2816. Собрано данных по модели: 2816
Страница 77 по бренду skoda по модели octavia собрана.
Количество совпадение на странице 77: 0. Количество собранных данных: 37
Собрано всего данных: 2853. Собрано данных по бренду: 2853. Собрано данных по модели: 2853
Страница 78 по бренду skoda по модели octavia собрана.
Количество совпадение на странице 78: 0. Количество собранных данных: 37
Собрано всего данных: 2890. Собрано данных по бренду: 2890. Собрано данных по модели: 2890
Страница 79 по бренду skoda по модели octavia собрана.
Количество совпадение на странице 79: 0. Количество собранных данных: 37
Собрано всего данных: 2927. Собрано данных по бренду: 2927. Собрано данных по модели: 2927
Страница 80 по бренду skoda по модели octavia собрана.
Количество совпадение на странице 80: 0. Количество собранных данных:

Страница 15 по бренду skoda по модели superb собрана.
Количество совпадение на странице 15: 0. Количество собранных данных: 37
Собрано всего данных: 4220. Собрано данных по бренду: 4220. Собрано данных по модели: 553
Страница 16 по бренду skoda по модели superb собрана.
Количество совпадение на странице 16: 0. Количество собранных данных: 27
Собрано всего данных: 4247. Собрано данных по бренду: 4247. Собрано данных по модели: 580
Страница 17 по бренду skoda по модели superb собрана.
Количество совпадение на странице 17: 0. Количество собранных данных: 0
Собрано всего данных: 4247. Собрано данных по бренду: 4247. Собрано данных по модели: 580
Прерывание.

Начало модели: octavia_rs.

Страница 1 по бренду skoda по модели octavia_rs собрана.
Количество совпадение на странице 1: 0. Количество собранных данных: 38
Собрано всего данных: 4285. Собрано данных по бренду: 4285. Собрано данных по модели: 38
Страница 2 по бренду skoda по модели octavia_rs собрана.
Количество совпадение на странице 

Страница 1 по бренду skoda по модели rapid собрана.
Количество совпадение на странице 1: 0. Количество собранных данных: 38
Собрано всего данных: 5364. Собрано данных по бренду: 5364. Собрано данных по модели: 38
Страница 2 по бренду skoda по модели rapid собрана.
Количество совпадение на странице 2: 0. Количество собранных данных: 38
Собрано всего данных: 5402. Собрано данных по бренду: 5402. Собрано данных по модели: 76
Страница 3 по бренду skoda по модели rapid собрана.
Количество совпадение на странице 3: 0. Количество собранных данных: 38
Собрано всего данных: 5440. Собрано данных по бренду: 5440. Собрано данных по модели: 114
Страница 4 по бренду skoda по модели rapid собрана.
Количество совпадение на странице 4: 0. Количество собранных данных: 38
Собрано всего данных: 5478. Собрано данных по бренду: 5478. Собрано данных по модели: 152
Страница 5 по бренду skoda по модели rapid собрана.
Количество совпадение на странице 5: 0. Количество собранных данных: 38
Собрано всего данных: 

...

Страница 8 по бренду mitsubishi по модели pajero собрана.
Количество совпадение на странице 8: 0. Количество собранных данных: 37
Собрано всего данных: 123417. Собрано данных по бренду: 5469. Собрано данных по модели: 297
Страница 9 по бренду mitsubishi по модели pajero собрана.
Количество совпадение на странице 9: 0. Количество собранных данных: 37
Собрано всего данных: 123454. Собрано данных по бренду: 5506. Собрано данных по модели: 334
Страница 10 по бренду mitsubishi по модели pajero собрана.
Количество совпадение на странице 10: 0. Количество собранных данных: 37
Собрано всего данных: 123491. Собрано данных по бренду: 5543. Собрано данных по модели: 371
Страница 11 по бренду mitsubishi по модели pajero собрана.
Количество совпадение на странице 11: 0. Количество собранных данных: 37
Собрано всего данных: 123528. Собрано данных по бренду: 5580. Собрано данных по модели: 408
Страница 12 по бренду mitsubishi по модели pajero собрана.
Количество совпадение на странице 12: 0. Количест

Страница 11 по бренду mitsubishi по модели galant собрана.
Количество совпадение на странице 11: 0. Количество собранных данных: 37
Собрано всего данных: 124667. Собрано данных по бренду: 6719. Собрано данных по модели: 408
Страница 12 по бренду mitsubishi по модели galant собрана.
Количество совпадение на странице 12: 0. Количество собранных данных: 37
Собрано всего данных: 124704. Собрано данных по бренду: 6756. Собрано данных по модели: 445
Страница 13 по бренду mitsubishi по модели galant собрана.
Количество совпадение на странице 13: 0. Количество собранных данных: 37
Собрано всего данных: 124741. Собрано данных по бренду: 6793. Собрано данных по модели: 482
Страница 14 по бренду mitsubishi по модели galant собрана.
Количество совпадение на странице 14: 0. Количество собранных данных: 37
Собрано всего данных: 124778. Собрано данных по бренду: 6830. Собрано данных по модели: 519
Страница 15 по бренду mitsubishi по модели galant собрана.
Количество совпадение на странице 15: 0. Коли

Страница 7 по бренду mitsubishi по модели colt собрана.
Количество совпадение на странице 7: 0. Количество собранных данных: 15
Собрано всего данных: 125819. Собрано данных по бренду: 7871. Собрано данных по модели: 235
Страница 8 по бренду mitsubishi по модели colt собрана.
Количество совпадение на странице 8: 0. Количество собранных данных: 0
Собрано всего данных: 125819. Собрано данных по бренду: 7871. Собрано данных по модели: 235
Прерывание.

Начало модели: carisma.

Страница 1 по бренду mitsubishi по модели carisma собрана.
Количество совпадение на странице 1: 0. Количество собранных данных: 38
Собрано всего данных: 125857. Собрано данных по бренду: 7909. Собрано данных по модели: 38
Страница 2 по бренду mitsubishi по модели carisma собрана.
Количество совпадение на странице 2: 1. Количество собранных данных: 38
Собрано всего данных: 125894. Собрано данных по бренду: 7946. Собрано данных по модели: 75
Страница 3 по бренду mitsubishi по модели carisma собрана.
Количество совпадени

Страница 1 по бренду mitsubishi по модели delica_d_5 собрана.
Количество совпадение на странице 1: 0. Количество собранных данных: 34
Собрано всего данных: 126644. Собрано данных по бренду: 8696. Собрано данных по модели: 34
Страница 2 по бренду mitsubishi по модели delica_d_5 собрана.
Количество совпадение на странице 2: 0. Количество собранных данных: 0
Собрано всего данных: 126644. Собрано данных по бренду: 8696. Собрано данных по модели: 34
Прерывание.

Начало модели: endeavor.

Страница 1 по бренду mitsubishi по модели endeavor собрана.
Количество совпадение на странице 1: 0. Количество собранных данных: 8
Собрано всего данных: 126652. Собрано данных по бренду: 8704. Собрано данных по модели: 8
Страница 2 по бренду mitsubishi по модели endeavor собрана.
Количество совпадение на странице 2: 0. Количество собранных данных: 0
Собрано всего данных: 126652. Собрано данных по бренду: 8704. Собрано данных по модели: 8
Прерывание.

Начало модели: delica.

Страница 1 по бренду mitsubishi п

Страница 1 по бренду mitsubishi по модели mirage собрана.
Количество совпадение на странице 1: 0. Количество собранных данных: 38
Собрано всего данных: 127103. Собрано данных по бренду: 9155. Собрано данных по модели: 38
Страница 2 по бренду mitsubishi по модели mirage собрана.
Количество совпадение на странице 2: 0. Количество собранных данных: 37
Собрано всего данных: 127140. Собрано данных по бренду: 9192. Собрано данных по модели: 75
Страница 3 по бренду mitsubishi по модели mirage собрана.
Количество совпадение на странице 3: 0. Количество собранных данных: 3
Собрано всего данных: 127143. Собрано данных по бренду: 9195. Собрано данных по модели: 78
Страница 4 по бренду mitsubishi по модели mirage собрана.
Количество совпадение на странице 4: 0. Количество собранных данных: 0
Собрано всего данных: 127143. Собрано данных по бренду: 9195. Собрано данных по модели: 78
Прерывание.

Начало модели: dingo.

Страница 1 по бренду mitsubishi по модели dingo собрана.
Количество совпадение на 

In [51]:
#Вывод url-адресов в файл
with open('Data/dict_train_url.json', 'w') as f:
    json.dump(dict_url, f)

In [78]:
#Парсинг
parsing(dict_url,'train')

Начало сбора данных по skoda, octavia. Всего url: 3667. Всего собрано: 0 / 127602.
Собрано 1 / 3667.
Собрано 2 / 3667.
Собрано 3 / 3667.
Собрано 4 / 3667.
Собрано 5 / 3667.
Собрано 6 / 3667.
Собрано 7 / 3667.
Собрано 8 / 3667.
Собрано 9 / 3667.
Собрано 10 / 3667.
Собрано 11 / 3667.
Собрано 12 / 3667.
Собрано 13 / 3667.
Собрано 14 / 3667.
Собрано 15 / 3667.
Собрано 16 / 3667.
Собрано 17 / 3667.
Собрано 18 / 3667.
Собрано 19 / 3667.
Собрано 20 / 3667.
Собрано 21 / 3667.
Собрано 22 / 3667.
Собрано 23 / 3667.
Собрано 24 / 3667.
Собрано 25 / 3667.
Собрано 26 / 3667.
Собрано 27 / 3667.
Собрано 28 / 3667.
Собрано 29 / 3667.
Собрано 30 / 3667.
Собрано 31 / 3667.
Собрано 32 / 3667.
Собрано 33 / 3667.
Собрано 34 / 3667.
Собрано 35 / 3667.
Собрано 36 / 3667.
Собрано 37 / 3667.
Собрано 38 / 3667.
Собрано 39 / 3667.
Собрано 40 / 3667.
Собрано 41 / 3667.
Собрано 42 / 3667.
Собрано 43 / 3667.
Собрано 44 / 3667.
Собрано 45 / 3667.
Собрано 46 / 3667.
Собрано 47 / 3667.
Собрано 48 / 3667.
Собрано 49 / 3

Собрано 412 / 3667.
Собрано 413 / 3667.
Собрано 414 / 3667.
Собрано 415 / 3667.
Собрано 416 / 3667.
Собрано 417 / 3667.
Собрано 418 / 3667.
Собрано 419 / 3667.
Собрано 420 / 3667.
Собрано 421 / 3667.
Собрано 422 / 3667.
Собрано 423 / 3667.
Собрано 424 / 3667.
Собрано 425 / 3667.
Собрано 426 / 3667.
Собрано 427 / 3667.
Собрано 428 / 3667.
Собрано 429 / 3667.
Собрано 430 / 3667.
Собрано 431 / 3667.
Собрано 432 / 3667.
Собрано 433 / 3667.
Собрано 434 / 3667.
Собрано 435 / 3667.
Собрано 436 / 3667.
Собрано 437 / 3667.
Собрано 438 / 3667.
Собрано 439 / 3667.
Собрано 440 / 3667.
Собрано 441 / 3667.
Собрано 442 / 3667.
Собрано 443 / 3667.
Собрано 444 / 3667.
Собрано 445 / 3667.
Собрано 446 / 3667.
Собрано 447 / 3667.
Собрано 448 / 3667.
Собрано 449 / 3667.
Собрано 450 / 3667.
Собрано 451 / 3667.
Собрано 452 / 3667.
Собрано 453 / 3667.
Собрано 454 / 3667.
Собрано 455 / 3667.
Собрано 456 / 3667.
Собрано 457 / 3667.
Собрано 458 / 3667.
Собрано 459 / 3667.
Собрано 460 / 3667.
Собрано 461 / 3667.


Собрано 818 / 3667.
Собрано 819 / 3667.
Собрано 820 / 3667.
Собрано 821 / 3667.
Собрано 822 / 3667.
Собрано 823 / 3667.
Собрано 824 / 3667.
Собрано 825 / 3667.
Собрано 826 / 3667.
Собрано 827 / 3667.
Собрано 828 / 3667.
Собрано 829 / 3667.
Собрано 830 / 3667.
Собрано 831 / 3667.
Собрано 832 / 3667.
Собрано 833 / 3667.
Собрано 834 / 3667.
Собрано 835 / 3667.
Собрано 836 / 3667.
Собрано 837 / 3667.
Собрано 838 / 3667.
Собрано 839 / 3667.
Собрано 840 / 3667.
Собрано 841 / 3667.
Собрано 842 / 3667.
Собрано 843 / 3667.
Собрано 844 / 3667.
Собрано 845 / 3667.
Собрано 846 / 3667.
Собрано 847 / 3667.
Собрано 848 / 3667.
Собрано 849 / 3667.
Собрано 850 / 3667.
Собрано 851 / 3667.
Собрано 852 / 3667.
Собрано 853 / 3667.
Собрано 854 / 3667.
Собрано 855 / 3667.
Собрано 856 / 3667.
Собрано 857 / 3667.
Собрано 858 / 3667.
Собрано 859 / 3667.
Собрано 860 / 3667.
Собрано 861 / 3667.
Собрано 862 / 3667.
Собрано 863 / 3667.
Собрано 864 / 3667.
Собрано 865 / 3667.
Собрано 866 / 3667.
Собрано 867 / 3667.


Собрано 1217 / 3667.
Собрано 1218 / 3667.
Собрано 1219 / 3667.
Собрано 1220 / 3667.
Собрано 1221 / 3667.
Собрано 1222 / 3667.
Собрано 1223 / 3667.
Собрано 1224 / 3667.
Собрано 1225 / 3667.
Собрано 1226 / 3667.
Собрано 1227 / 3667.
Собрано 1228 / 3667.
Собрано 1229 / 3667.
Собрано 1230 / 3667.
Собрано 1231 / 3667.
Собрано 1232 / 3667.
Собрано 1233 / 3667.
Собрано 1234 / 3667.
Собрано 1235 / 3667.
Собрано 1236 / 3667.
Собрано 1237 / 3667.
Собрано 1238 / 3667.
Собрано 1239 / 3667.
Собрано 1240 / 3667.
Собрано 1241 / 3667.
Собрано 1242 / 3667.
Собрано 1243 / 3667.
Собрано 1244 / 3667.
Собрано 1245 / 3667.
Собрано 1246 / 3667.
Собрано 1247 / 3667.
Собрано 1248 / 3667.
Собрано 1249 / 3667.
Собрано 1250 / 3667.
Собрано 1251 / 3667.
Собрано 1252 / 3667.
Собрано 1253 / 3667.
Собрано 1254 / 3667.
Собрано 1255 / 3667.
Собрано 1256 / 3667.
Собрано 1257 / 3667.
Собрано 1258 / 3667.
Собрано 1259 / 3667.
Собрано 1260 / 3667.
Собрано 1261 / 3667.
Собрано 1262 / 3667.
Собрано 1263 / 3667.
Собрано 1264 

Собрано 1608 / 3667.
Собрано 1609 / 3667.
Собрано 1610 / 3667.
Собрано 1611 / 3667.
Собрано 1612 / 3667.
Собрано 1613 / 3667.
Собрано 1614 / 3667.
Собрано 1615 / 3667.
Собрано 1616 / 3667.
Собрано 1617 / 3667.
Собрано 1618 / 3667.
Собрано 1619 / 3667.
Собрано 1620 / 3667.
Собрано 1621 / 3667.
Собрано 1622 / 3667.
Собрано 1623 / 3667.
Собрано 1624 / 3667.
Собрано 1625 / 3667.
Собрано 1626 / 3667.
Собрано 1627 / 3667.
Собрано 1628 / 3667.
Собрано 1629 / 3667.
Собрано 1630 / 3667.
Собрано 1631 / 3667.
Собрано 1632 / 3667.
Собрано 1633 / 3667.
Собрано 1634 / 3667.
Собрано 1635 / 3667.
Собрано 1636 / 3667.
Собрано 1637 / 3667.
Собрано 1638 / 3667.
Собрано 1639 / 3667.
Собрано 1640 / 3667.
Собрано 1641 / 3667.
Собрано 1642 / 3667.
Собрано 1643 / 3667.
Собрано 1644 / 3667.
Собрано 1645 / 3667.
Собрано 1646 / 3667.
Собрано 1647 / 3667.
Собрано 1648 / 3667.
Собрано 1649 / 3667.
Собрано 1650 / 3667.
Собрано 1651 / 3667.
Собрано 1652 / 3667.
Собрано 1653 / 3667.
Собрано 1654 / 3667.
Собрано 1655 

...

Собрано 137 / 235.
Собрано 138 / 235.
Собрано 139 / 235.
Собрано 140 / 235.
Собрано 141 / 235.
Собрано 142 / 235.
Собрано 143 / 235.
Собрано 144 / 235.
Собрано 145 / 235.
Собрано 146 / 235.
Собрано 147 / 235.
Собрано 148 / 235.
Собрано 149 / 235.
Собрано 150 / 235.
Собрано 151 / 235.
Собрано 152 / 235.
Собрано 153 / 235.
Собрано 154 / 235.
Собрано 155 / 235.
Собрано 156 / 235.
Собрано 157 / 235.
Собрано 158 / 235.
Собрано 159 / 235.
Собрано 160 / 235.
Собрано 161 / 235.
Собрано 162 / 235.
Собрано 163 / 235.
Собрано 164 / 235.
Собрано 165 / 235.
Собрано 166 / 235.
Собрано 167 / 235.
Собрано 168 / 235.
Собрано 169 / 235.
Собрано 170 / 235.
Собрано 171 / 235.
Собрано 172 / 235.
Собрано 173 / 235.
Собрано 174 / 235.
Собрано 175 / 235.
Собрано 176 / 235.
Собрано 177 / 235.
Собрано 178 / 235.
Собрано 179 / 235.
Собрано 180 / 235.
Собрано 181 / 235.
Собрано 182 / 235.
Собрано 183 / 235.
Собрано 184 / 235.
Собрано 185 / 235.
Собрано 186 / 235.
Собрано 187 / 235.
Собрано 188 / 235.
Собрано 189 

Собрано 335 / 435.
Собрано 336 / 435.
Собрано 337 / 435.
Собрано 338 / 435.
Собрано 339 / 435.
Собрано 340 / 435.
Собрано 341 / 435.
Собрано 342 / 435.
Собрано 343 / 435.
Собрано 344 / 435.
Собрано 345 / 435.
Собрано 346 / 435.
Собрано 347 / 435.
Собрано 348 / 435.
Собрано 349 / 435.
Собрано 350 / 435.
Собрано 351 / 435.
Собрано 352 / 435.
Собрано 353 / 435.
Собрано 354 / 435.
Собрано 355 / 435.
Собрано 356 / 435.
Собрано 357 / 435.
Собрано 358 / 435.
Собрано 359 / 435.
Собрано 360 / 435.
Собрано 361 / 435.
Собрано 362 / 435.
Собрано 363 / 435.
Собрано 364 / 435.
Собрано 365 / 435.
Собрано 366 / 435.
Собрано 367 / 435.
Собрано 368 / 435.
Собрано 369 / 435.
Собрано 370 / 435.
Собрано 371 / 435.
Собрано 372 / 435.
Собрано 373 / 435.
Собрано 374 / 435.
Собрано 375 / 435.
Собрано 376 / 435.
Собрано 377 / 435.
Собрано 378 / 435.
Собрано 379 / 435.
Собрано 380 / 435.
Собрано 381 / 435.
Собрано 382 / 435.
Собрано 383 / 435.
Собрано 384 / 435.
Собрано 385 / 435.
Собрано 386 / 435.
Собрано 387 

Собрано 59 / 70.
Собрано 60 / 70.
Собрано 61 / 70.
Собрано 62 / 70.
Собрано 63 / 70.
Собрано 64 / 70.
Собрано 65 / 70.
Собрано 66 / 70.
Собрано 67 / 70.
Собрано 68 / 70.
Собрано 69 / 70.
Собрано 70 / 70.
Начало сбора данных по mitsubishi, minicab. Всего url: 9. Всего собрано: 126601 / 127602.
Собрано 1 / 9.
Собрано 2 / 9.
Собрано 3 / 9.
Собрано 4 / 9.
Собрано 5 / 9.
Собрано 6 / 9.
Собрано 7 / 9.
Собрано 8 / 9.
Собрано 9 / 9.
Начало сбора данных по mitsubishi, delica_d_5. Всего url: 34. Всего собрано: 126610 / 127602.
Собрано 1 / 34.
Собрано 2 / 34.
Собрано 3 / 34.
Собрано 4 / 34.
Собрано 5 / 34.
Собрано 6 / 34.
Собрано 7 / 34.
Собрано 8 / 34.
Собрано 9 / 34.
Собрано 10 / 34.
Собрано 11 / 34.
Собрано 12 / 34.
Собрано 13 / 34.
Собрано 14 / 34.
Собрано 15 / 34.
Собрано 16 / 34.
Собрано 17 / 34.
Собрано 18 / 34.
Собрано 19 / 34.
Собрано 20 / 34.
Собрано 21 / 34.
Собрано 22 / 34.
Собрано 23 / 34.
Собрано 24 / 34.
Собрано 25 / 34.
Собрано 26 / 34.
Собрано 27 / 34.
Собрано 28 / 34.
Собрано 29

Собрано 34 / 87.
Собрано 35 / 87.
Собрано 36 / 87.
Собрано 37 / 87.
Собрано 38 / 87.
Собрано 39 / 87.
Собрано 40 / 87.
Собрано 41 / 87.
Собрано 42 / 87.
Собрано 43 / 87.
Собрано 44 / 87.
Собрано 45 / 87.
Собрано 46 / 87.
Собрано 47 / 87.
Собрано 48 / 87.
Собрано 49 / 87.
Собрано 50 / 87.
Собрано 51 / 87.
Собрано 52 / 87.
Собрано 53 / 87.
Собрано 54 / 87.
Собрано 55 / 87.
Собрано 56 / 87.
Собрано 57 / 87.
Собрано 58 / 87.
Собрано 59 / 87.
Собрано 60 / 87.
Собрано 61 / 87.
Собрано 62 / 87.
Собрано 63 / 87.
Собрано 64 / 87.
Собрано 65 / 87.
Собрано 66 / 87.
Собрано 67 / 87.
Собрано 68 / 87.
Собрано 69 / 87.
Собрано 70 / 87.
Собрано 71 / 87.
Собрано 72 / 87.
Собрано 73 / 87.
Собрано 74 / 87.
Собрано 75 / 87.
Собрано 76 / 87.
Собрано 77 / 87.
Собрано 78 / 87.
Собрано 79 / 87.
Собрано 80 / 87.
Собрано 81 / 87.
Собрано 82 / 87.
Собрано 83 / 87.
Собрано 84 / 87.
Собрано 85 / 87.
Собрано 86 / 87.
Собрано 87 / 87.
Начало сбора данных по mitsubishi, l400. Всего url: 14. Всего собрано: 127051 / 12

Собрано 2 / 107.
Собрано 3 / 107.
Собрано 4 / 107.
Собрано 5 / 107.
Собрано 6 / 107.
Собрано 7 / 107.
Собрано 8 / 107.
Собрано 9 / 107.
Собрано 10 / 107.
Собрано 11 / 107.
Собрано 12 / 107.
Собрано 13 / 107.
Собрано 14 / 107.
Собрано 15 / 107.
Собрано 16 / 107.
Собрано 17 / 107.
Собрано 18 / 107.
Собрано 19 / 107.
Собрано 20 / 107.
Собрано 21 / 107.
Собрано 22 / 107.
Собрано 23 / 107.
Собрано 24 / 107.
Собрано 25 / 107.
Собрано 26 / 107.
Собрано 27 / 107.
Собрано 28 / 107.
Собрано 29 / 107.
Собрано 30 / 107.
Собрано 31 / 107.
Собрано 32 / 107.
Собрано 33 / 107.
Собрано 34 / 107.
Собрано 35 / 107.
Собрано 36 / 107.
Собрано 37 / 107.
Собрано 38 / 107.
Собрано 39 / 107.
Собрано 40 / 107.
Собрано 41 / 107.
Собрано 42 / 107.
Собрано 43 / 107.
Собрано 44 / 107.
Собрано 45 / 107.
Собрано 46 / 107.
Собрано 47 / 107.
Собрано 48 / 107.
Собрано 49 / 107.
Собрано 50 / 107.
Собрано 51 / 107.
Собрано 52 / 107.
Собрано 53 / 107.
Собрано 54 / 107.
Собрано 55 / 107.
Собрано 56 / 107.
Собрано 57 / 107.


In [81]:
#Объединение
union_data(dict_url,'train')

# 4.Парсинг данных test (старая версия)

In [38]:
#ПЕРЕПИСАТЬ

#Сбор адресов
dict_url = collections.defaultdict(list)
for ind in df_test.index:
    dict_url[df_test.loc[ind,'brand'].lower()] += [df_test.loc[ind,'car_url']]
dict_url = dict(dict_url)

In [39]:
#Вывод url-адресов в файл
with open('Data/dict_test_url.json', 'w') as f:
    json.dump(dict_url, f)

In [ ]:
#Парсинг
parsing(dict_url,'test')
#Объединение
union_data(dict_url,'test')

# 5.Парсинг данных brand&model (about price)

In [100]:
#Составление полного списка брендов и моделей
list_brand_model = []
for url in df_test['car_url']:
    list_brand_model += [url.split('/')[6]+'||'+url.split('/')[7]]
#Удаление повторений
list_brand_model = list(set(list_brand_model))

In [101]:
mas = []
#Перебор
for i,l in enumerate(list_brand_model):
    #Составление url
    brand, model = l.split('||')
    url = 'https://auto.ru/stats/cars/' + brand + '/' + model + '/'
    #Загрузка страницы поиска
    response = requests.get(url)
    if response.status_code == 200:
        tree = html.fromstring(response.content)
        #Сбор данных
        xpath_price = tree.xpath('//div[@class="StatsAverage__price"]//text()')
        xpath_price_title = tree.xpath('//div[@class="StatsAverage__title-info"]//text()')
        xpath_price_per = tree.xpath('//div[@class="StatsPricePerAge__title-info"]//text()')
        xpath_day_mean = tree.xpath('//div[@class="StatsAverageTimeSale__duration"]//text()')
        xpath_day_opt = tree.xpath('//div[@class="StatsAverageTimeSaleService__duration"]//text()')
        xpath_rank = tree.xpath('//div[@class="CrossLinks__rating"]//text()')
        mas += [[url,brand,model,
                 xpath_price,xpath_price_title,xpath_price_per,
                 xpath_day_mean,xpath_day_opt,xpath_rank]]
        print('Собрано {} / {}. Цена: {}. {}.'.format(i,len(list_brand_model),xpath_price, url))

Собрано 0 / 544. Цена: ['2\xa0734\xa0993', '\xa0', '₽']. https://auto.ru/stats/cars/toyota/land_cruiser_prado/.
Собрано 1 / 544. Цена: []. https://auto.ru/stats/cars/toyota/ipsum/.
Собрано 2 / 544. Цена: []. https://auto.ru/stats/cars/toyota/sprinter/.
Собрано 3 / 544. Цена: []. https://auto.ru/stats/cars/volvo/v60/.
Собрано 4 / 544. Цена: []. https://auto.ru/stats/cars/honda/partner/.
Собрано 5 / 544. Цена: ['1\xa0153\xa0793', '\xa0', '₽']. https://auto.ru/stats/cars/mitsubishi/l200/.
Собрано 6 / 544. Цена: ['1\xa0711\xa0746', '\xa0', '₽']. https://auto.ru/stats/cars/nissan/patrol/.
Собрано 7 / 544. Цена: ['2\xa0424\xa0316', '\xa0', '₽']. https://auto.ru/stats/cars/lexus/nx/.
Собрано 8 / 544. Цена: ['786\xa0975', '\xa0', '₽']. https://auto.ru/stats/cars/skoda/octavia/.
Собрано 9 / 544. Цена: []. https://auto.ru/stats/cars/toyota/regius/.
Собрано 10 / 544. Цена: ['1\xa0992\xa0630', '\xa0', '₽']. https://auto.ru/stats/cars/infiniti/qx50/.
Собрано 11 / 544. Цена: []. https://auto.ru/stat

Собрано 99 / 544. Цена: []. https://auto.ru/stats/cars/audi/rs3/.
Собрано 100 / 544. Цена: ['4\xa0328\xa0181', '\xa0', '₽']. https://auto.ru/stats/cars/mercedes/glc_klasse_amg/.
Собрано 101 / 544. Цена: []. https://auto.ru/stats/cars/honda/city/.
Собрано 102 / 544. Цена: ['877\xa0392', '\xa0', '₽']. https://auto.ru/stats/cars/volvo/s60/.
Собрано 103 / 544. Цена: ['3\xa0377\xa0499', '\xa0', '₽']. https://auto.ru/stats/cars/mercedes/a_klasse_amg/.
Собрано 104 / 544. Цена: []. https://auto.ru/stats/cars/audi/rs4/.
Собрано 105 / 544. Цена: ['1\xa0520\xa0000', '\xa0', '₽']. https://auto.ru/stats/cars/bmw/2activetourer/.
Собрано 106 / 544. Цена: []. https://auto.ru/stats/cars/nissan/200sx/.
Собрано 107 / 544. Цена: []. https://auto.ru/stats/cars/skoda/favorit/.
Собрано 108 / 544. Цена: ['550\xa0145', '\xa0', '₽']. https://auto.ru/stats/cars/nissan/note/.
Собрано 109 / 544. Цена: []. https://auto.ru/stats/cars/volkswagen/type_1/.
Собрано 110 / 544. Цена: []. https://auto.ru/stats/cars/mitsubi

Собрано 197 / 544. Цена: []. https://auto.ru/stats/cars/mitsubishi/sigma/.
Собрано 198 / 544. Цена: ['2\xa0210\xa0952', '\xa0', '₽']. https://auto.ru/stats/cars/toyota/harrier/.
Собрано 199 / 544. Цена: ['2\xa0647\xa0455', '\xa0', '₽']. https://auto.ru/stats/cars/lexus/rx/.
Собрано 200 / 544. Цена: ['1\xa0338\xa0135', '\xa0', '₽']. https://auto.ru/stats/cars/audi/q3/.
Собрано 201 / 544. Цена: []. https://auto.ru/stats/cars/mitsubishi/lancer_evolution/.
Собрано 202 / 544. Цена: ['3\xa0156\xa0541', '\xa0', '₽']. https://auto.ru/stats/cars/mercedes/s_klasse/.
Собрано 203 / 544. Цена: ['1\xa0800\xa0833', '\xa0', '₽']. https://auto.ru/stats/cars/mitsubishi/eclipse_cross/.
Собрано 204 / 544. Цена: []. https://auto.ru/stats/cars/mercedes/w111/.
Собрано 205 / 544. Цена: []. https://auto.ru/stats/cars/mercedes/vaneo/.
Собрано 206 / 544. Цена: []. https://auto.ru/stats/cars/mercedes/w114/.
Собрано 207 / 544. Цена: ['1\xa0558\xa0544', '\xa0', '₽']. https://auto.ru/stats/cars/toyota/rav_4/.
Собран

Собрано 296 / 544. Цена: []. https://auto.ru/stats/cars/toyota/avensis_verso/.
Собрано 297 / 544. Цена: ['2\xa0025\xa0472', '\xa0', '₽']. https://auto.ru/stats/cars/toyota/sienna/.
Собрано 298 / 544. Цена: []. https://auto.ru/stats/cars/toyota/succeed/.
Собрано 299 / 544. Цена: []. https://auto.ru/stats/cars/toyota/opa/.
Собрано 300 / 544. Цена: []. https://auto.ru/stats/cars/infiniti/q30/.
Собрано 301 / 544. Цена: ['2\xa0249\xa0066', '\xa0', '₽']. https://auto.ru/stats/cars/mercedes/m_klasse_amg/.
Собрано 302 / 544. Цена: ['3\xa0609\xa0754', '\xa0', '₽']. https://auto.ru/stats/cars/toyota/land_cruiser/.
Собрано 303 / 544. Цена: ['2\xa0193\xa0914', '\xa0', '₽']. https://auto.ru/stats/cars/volkswagen/touareg/.
Собрано 304 / 544. Цена: []. https://auto.ru/stats/cars/toyota/platz/.
Собрано 305 / 544. Цена: []. https://auto.ru/stats/cars/lexus/sc/.
Собрано 306 / 544. Цена: []. https://auto.ru/stats/cars/toyota/funcargo/.
Собрано 307 / 544. Цена: []. https://auto.ru/stats/cars/toyota/cynos/

Собрано 395 / 544. Цена: ['1\xa0233\xa0328', '\xa0', '₽']. https://auto.ru/stats/cars/honda/stepwagon/.
Собрано 396 / 544. Цена: ['572\xa0506', '\xa0', '₽']. https://auto.ru/stats/cars/toyota/vitz/.
Собрано 397 / 544. Цена: []. https://auto.ru/stats/cars/volvo/v70/.
Собрано 398 / 544. Цена: []. https://auto.ru/stats/cars/mitsubishi/aspire/.
Собрано 399 / 544. Цена: []. https://auto.ru/stats/cars/toyota/corona/.
Собрано 400 / 544. Цена: []. https://auto.ru/stats/cars/nissan/liberty/.
Собрано 401 / 544. Цена: []. https://auto.ru/stats/cars/toyota/echo/.
Собрано 402 / 544. Цена: ['1\xa0873\xa0333', '\xa0', '₽']. https://auto.ru/stats/cars/toyota/crown/.
Собрано 403 / 544. Цена: ['2\xa0099\xa0022', '\xa0', '₽']. https://auto.ru/stats/cars/audi/allroad/.
Собрано 404 / 544. Цена: ['5\xa0498\xa0670', '\xa0', '₽']. https://auto.ru/stats/cars/mercedes/gle_klasse_coupe_amg/.
Собрано 405 / 544. Цена: []. https://auto.ru/stats/cars/volkswagen/golf_r32/.
Собрано 406 / 544. Цена: []. https://auto.ru

Собрано 493 / 544. Цена: []. https://auto.ru/stats/cars/honda/saber/.
Собрано 494 / 544. Цена: ['1\xa0242\xa0897', '\xa0', '₽']. https://auto.ru/stats/cars/bmw/x1/.
Собрано 495 / 544. Цена: []. https://auto.ru/stats/cars/toyota/aristo/.
Собрано 496 / 544. Цена: []. https://auto.ru/stats/cars/volvo/v40/.
Собрано 497 / 544. Цена: []. https://auto.ru/stats/cars/toyota/previa/.
Собрано 498 / 544. Цена: ['4\xa0697\xa0117', '\xa0', '₽']. https://auto.ru/stats/cars/lexus/lx/.
Собрано 499 / 544. Цена: ['512\xa0218', '\xa0', '₽']. https://auto.ru/stats/cars/mitsubishi/lancer/.
Собрано 500 / 544. Цена: []. https://auto.ru/stats/cars/toyota/town_ace/.
Собрано 501 / 544. Цена: []. https://auto.ru/stats/cars/volvo/740/.
Собрано 502 / 544. Цена: []. https://auto.ru/stats/cars/bmw/e3/.
Собрано 503 / 544. Цена: []. https://auto.ru/stats/cars/volkswagen/corrado/.
Собрано 504 / 544. Цена: []. https://auto.ru/stats/cars/mitsubishi/l300/.
Собрано 505 / 544. Цена: ['708\xa0275', '\xa0', '₽']. https://auto.

In [102]:
#Сбор и выгрузка данных
df_price_autoru = pd.DataFrame(mas,columns=['url','brand','model','price_autoru','price_title','price_per','day_mean','day_opt','rank'])
df_price_autoru.to_csv('Data/price_auto_ru.csv')

# 6.Парсинг данных brand&model (about rating)

In [106]:
mas = []
#Перебор
for i,l in enumerate(list_brand_model):
    #Составление url
    brand, model = l.split('||')
    url = 'https://auto.ru/reviews/cars/' + brand + '/' + model + '/'
    #Загрузка страницы поиска
    response = requests.get(url)
    if response.status_code == 200:
        tree = html.fromstring(response.content)
        #Сбор данных
        xpath_rating = tree.xpath('//div[@class="ReviewRating__number"]//text()')
        xpath_mas_rating = tree.xpath('//span[@class="ReviewsSummaryFull__ratingValueWithFeatures"]//text()')
        xpath_plus_minus = tree.xpath('//div[@class="ReviewsSummaryFull__reviews__features__top_total"]//text()')
        xpath_mas_plus = tree.xpath('//span[@class="ReviewsSummaryFull__reviews__features_plus_count"]//text()')
        xpath_mas_minus = tree.xpath('//span[@class="ReviewsSummaryFull__reviews__features_minus_count"]//text()')

        mas += [[url,brand,model,
                 xpath_rating,xpath_mas_rating,xpath_plus_minus,
                 xpath_mas_plus,xpath_mas_minus]]
        print('Собрано {} / {}.'.format(i,len(list_brand_model)))

Собрано 0 / 544.
Собрано 1 / 544.
Собрано 2 / 544.
Собрано 3 / 544.
Собрано 4 / 544.
Собрано 5 / 544.
Собрано 6 / 544.
Собрано 7 / 544.
Собрано 8 / 544.
Собрано 9 / 544.
Собрано 10 / 544.
Собрано 11 / 544.
Собрано 12 / 544.
Собрано 13 / 544.
Собрано 14 / 544.
Собрано 15 / 544.
Собрано 16 / 544.
Собрано 17 / 544.
Собрано 18 / 544.
Собрано 19 / 544.
Собрано 20 / 544.
Собрано 21 / 544.
Собрано 22 / 544.
Собрано 23 / 544.
Собрано 24 / 544.
Собрано 25 / 544.
Собрано 26 / 544.
Собрано 27 / 544.
Собрано 28 / 544.
Собрано 29 / 544.
Собрано 30 / 544.
Собрано 31 / 544.
Собрано 32 / 544.
Собрано 33 / 544.
Собрано 34 / 544.
Собрано 35 / 544.
Собрано 36 / 544.
Собрано 37 / 544.
Собрано 38 / 544.
Собрано 39 / 544.
Собрано 40 / 544.
Собрано 41 / 544.
Собрано 42 / 544.
Собрано 43 / 544.
Собрано 44 / 544.
Собрано 45 / 544.
Собрано 46 / 544.
Собрано 47 / 544.
Собрано 48 / 544.
Собрано 49 / 544.
Собрано 50 / 544.
Собрано 51 / 544.
Собрано 52 / 544.
Собрано 53 / 544.
Собрано 54 / 544.
Собрано 55 / 544.
Со

Собрано 437 / 544.
Собрано 438 / 544.
Собрано 439 / 544.
Собрано 440 / 544.
Собрано 441 / 544.
Собрано 442 / 544.
Собрано 443 / 544.
Собрано 444 / 544.
Собрано 445 / 544.
Собрано 446 / 544.
Собрано 447 / 544.
Собрано 448 / 544.
Собрано 449 / 544.
Собрано 450 / 544.
Собрано 451 / 544.
Собрано 452 / 544.
Собрано 453 / 544.
Собрано 454 / 544.
Собрано 455 / 544.
Собрано 456 / 544.
Собрано 457 / 544.
Собрано 458 / 544.
Собрано 459 / 544.
Собрано 460 / 544.
Собрано 461 / 544.
Собрано 462 / 544.
Собрано 463 / 544.
Собрано 464 / 544.
Собрано 465 / 544.
Собрано 466 / 544.
Собрано 467 / 544.
Собрано 468 / 544.
Собрано 469 / 544.
Собрано 470 / 544.
Собрано 471 / 544.
Собрано 472 / 544.
Собрано 473 / 544.
Собрано 474 / 544.
Собрано 475 / 544.
Собрано 476 / 544.
Собрано 477 / 544.
Собрано 478 / 544.
Собрано 479 / 544.
Собрано 480 / 544.
Собрано 481 / 544.
Собрано 482 / 544.
Собрано 483 / 544.
Собрано 484 / 544.
Собрано 485 / 544.
Собрано 486 / 544.
Собрано 487 / 544.
Собрано 488 / 544.
Собрано 489 

In [109]:
#Сбор и выгрузка данных
df_rating_autoru = pd.DataFrame(mas,columns=['url','brand','model','rating','mas_rating','plus_minus','mas_plus','mas_minus'])
df_rating_autoru.to_csv('Data/rating_auto_ru.csv')

# 7.Парсинг данных train&test (date)

In [7]:
#Чтение url-адресов в файл
with open('Data/dict_train_url.json', 'r') as f:
    dict_url_train = json.load(f)

In [11]:
#Перебор train
for brand in dict_url_train:
        for model in dict_url_train[brand]:
            print('Начало: {} | {}.'.format(brand,model))
            mas = []
            l = len(dict_url_train[brand][model])
            for i, url in enumerate(dict_url_train[brand][model]):
                print('{} / {}'.format(i+1,l))
                response = requests.get(url)
                if response.status_code == 200:
                    tree = html.fromstring(response.content)
                    #Сбор данных
                    xpath_date = tree.xpath('//div[contains(@title,"Дата")]//text()')
                    mas += [[brand,model,url,xpath_date]]
            #Вывод в файл промежуточного результата
            pd.DataFrame(mas,columns=['brand','model','url','xpath_date']).to_csv('Data/train_date/train_'+brand+'_'+model+'.csv')

Начало: nissan | qashqai.
1 / 2224
2 / 2224
3 / 2224
4 / 2224
5 / 2224
6 / 2224
7 / 2224
8 / 2224
9 / 2224
10 / 2224
11 / 2224
12 / 2224
13 / 2224
14 / 2224
15 / 2224
16 / 2224
17 / 2224
18 / 2224
19 / 2224
20 / 2224
21 / 2224
22 / 2224
23 / 2224
24 / 2224
25 / 2224
26 / 2224
27 / 2224
28 / 2224
29 / 2224
30 / 2224
31 / 2224
32 / 2224
33 / 2224
34 / 2224
35 / 2224
36 / 2224
37 / 2224
38 / 2224
39 / 2224
40 / 2224
41 / 2224
42 / 2224
43 / 2224
44 / 2224
45 / 2224
46 / 2224
47 / 2224
48 / 2224
49 / 2224
50 / 2224
51 / 2224
52 / 2224
53 / 2224
54 / 2224
55 / 2224
56 / 2224
57 / 2224
58 / 2224
59 / 2224
60 / 2224
61 / 2224
62 / 2224
63 / 2224
64 / 2224
65 / 2224
66 / 2224
67 / 2224
68 / 2224
69 / 2224
70 / 2224
71 / 2224
72 / 2224
73 / 2224
74 / 2224
75 / 2224
76 / 2224
77 / 2224
78 / 2224
79 / 2224
80 / 2224
81 / 2224
82 / 2224
83 / 2224
84 / 2224
85 / 2224
86 / 2224
87 / 2224
88 / 2224
89 / 2224
90 / 2224
91 / 2224
92 / 2224
93 / 2224
94 / 2224
95 / 2224
96 / 2224
97 / 2224
98 / 2224
99 

754 / 2224
755 / 2224
756 / 2224
757 / 2224
758 / 2224
759 / 2224
760 / 2224
761 / 2224
762 / 2224
763 / 2224
764 / 2224
765 / 2224
766 / 2224
767 / 2224
768 / 2224
769 / 2224
770 / 2224
771 / 2224
772 / 2224
773 / 2224
774 / 2224
775 / 2224
776 / 2224
777 / 2224
778 / 2224
779 / 2224
780 / 2224
781 / 2224
782 / 2224
783 / 2224
784 / 2224
785 / 2224
786 / 2224
787 / 2224
788 / 2224
789 / 2224
790 / 2224
791 / 2224
792 / 2224
793 / 2224
794 / 2224
795 / 2224
796 / 2224
797 / 2224
798 / 2224
799 / 2224
800 / 2224
801 / 2224
802 / 2224
803 / 2224
804 / 2224
805 / 2224
806 / 2224
807 / 2224
808 / 2224
809 / 2224
810 / 2224
811 / 2224
812 / 2224
813 / 2224
814 / 2224
815 / 2224
816 / 2224
817 / 2224
818 / 2224
819 / 2224
820 / 2224
821 / 2224
822 / 2224
823 / 2224
824 / 2224
825 / 2224
826 / 2224
827 / 2224
828 / 2224
829 / 2224
830 / 2224
831 / 2224
832 / 2224
833 / 2224
834 / 2224
835 / 2224
836 / 2224
837 / 2224
838 / 2224
839 / 2224
840 / 2224
841 / 2224
842 / 2224
843 / 2224
844 / 2224

1458 / 2224
1459 / 2224
1460 / 2224
1461 / 2224
1462 / 2224
1463 / 2224
1464 / 2224
1465 / 2224
1466 / 2224
1467 / 2224
1468 / 2224
1469 / 2224
1470 / 2224
1471 / 2224
1472 / 2224
1473 / 2224
1474 / 2224
1475 / 2224
1476 / 2224
1477 / 2224
1478 / 2224
1479 / 2224
1480 / 2224
1481 / 2224
1482 / 2224
1483 / 2224
1484 / 2224
1485 / 2224
1486 / 2224
1487 / 2224
1488 / 2224
1489 / 2224
1490 / 2224
1491 / 2224
1492 / 2224
1493 / 2224
1494 / 2224
1495 / 2224
1496 / 2224
1497 / 2224
1498 / 2224
1499 / 2224
1500 / 2224
1501 / 2224
1502 / 2224
1503 / 2224
1504 / 2224
1505 / 2224
1506 / 2224
1507 / 2224
1508 / 2224
1509 / 2224
1510 / 2224
1511 / 2224
1512 / 2224
1513 / 2224
1514 / 2224
1515 / 2224
1516 / 2224
1517 / 2224
1518 / 2224
1519 / 2224
1520 / 2224
1521 / 2224
1522 / 2224
1523 / 2224
1524 / 2224
1525 / 2224
1526 / 2224
1527 / 2224
1528 / 2224
1529 / 2224
1530 / 2224
1531 / 2224
1532 / 2224
1533 / 2224
1534 / 2224
1535 / 2224
1536 / 2224
1537 / 2224
1538 / 2224
1539 / 2224
1540 / 2224
1541

2141 / 2224
2142 / 2224
2143 / 2224
2144 / 2224
2145 / 2224
2146 / 2224
2147 / 2224
2148 / 2224
2149 / 2224
2150 / 2224
2151 / 2224
2152 / 2224
2153 / 2224
2154 / 2224
2155 / 2224
2156 / 2224
2157 / 2224
2158 / 2224
2159 / 2224
2160 / 2224
2161 / 2224
2162 / 2224
2163 / 2224
2164 / 2224
2165 / 2224
2166 / 2224
2167 / 2224
2168 / 2224
2169 / 2224
2170 / 2224
2171 / 2224
2172 / 2224
2173 / 2224
2174 / 2224
2175 / 2224
2176 / 2224
2177 / 2224
2178 / 2224
2179 / 2224
2180 / 2224
2181 / 2224
2182 / 2224
2183 / 2224
2184 / 2224
2185 / 2224
2186 / 2224
2187 / 2224
2188 / 2224
2189 / 2224
2190 / 2224
2191 / 2224
2192 / 2224
2193 / 2224
2194 / 2224
2195 / 2224
2196 / 2224
2197 / 2224
2198 / 2224
2199 / 2224
2200 / 2224
2201 / 2224
2202 / 2224
2203 / 2224
2204 / 2224
2205 / 2224
2206 / 2224
2207 / 2224
2208 / 2224
2209 / 2224
2210 / 2224
2211 / 2224
2212 / 2224
2213 / 2224
2214 / 2224
2215 / 2224
2216 / 2224
2217 / 2224
2218 / 2224
2219 / 2224
2220 / 2224
2221 / 2224
2222 / 2224
2223 / 2224
2224

556 / 2069
557 / 2069
558 / 2069
559 / 2069
560 / 2069
561 / 2069
562 / 2069
563 / 2069
564 / 2069
565 / 2069
566 / 2069
567 / 2069
568 / 2069
569 / 2069
570 / 2069
571 / 2069
572 / 2069
573 / 2069
574 / 2069
575 / 2069
576 / 2069
577 / 2069
578 / 2069
579 / 2069
580 / 2069
581 / 2069
582 / 2069
583 / 2069
584 / 2069
585 / 2069
586 / 2069
587 / 2069
588 / 2069
589 / 2069
590 / 2069
591 / 2069
592 / 2069
593 / 2069
594 / 2069
595 / 2069
596 / 2069
597 / 2069
598 / 2069
599 / 2069
600 / 2069
601 / 2069
602 / 2069
603 / 2069
604 / 2069
605 / 2069
606 / 2069
607 / 2069
608 / 2069
609 / 2069
610 / 2069
611 / 2069
612 / 2069
613 / 2069
614 / 2069
615 / 2069
616 / 2069
617 / 2069
618 / 2069
619 / 2069
620 / 2069
621 / 2069
622 / 2069
623 / 2069
624 / 2069
625 / 2069
626 / 2069
627 / 2069
628 / 2069
629 / 2069
630 / 2069
631 / 2069
632 / 2069
633 / 2069
634 / 2069
635 / 2069
636 / 2069
637 / 2069
638 / 2069
639 / 2069
640 / 2069
641 / 2069
642 / 2069
643 / 2069
644 / 2069
645 / 2069
646 / 2069

...

528 / 1050
529 / 1050
530 / 1050
531 / 1050
532 / 1050
533 / 1050
534 / 1050
535 / 1050
536 / 1050
537 / 1050
538 / 1050
539 / 1050
540 / 1050
541 / 1050
542 / 1050
543 / 1050
544 / 1050
545 / 1050
546 / 1050
547 / 1050
548 / 1050
549 / 1050
550 / 1050
551 / 1050
552 / 1050
553 / 1050
554 / 1050
555 / 1050
556 / 1050
557 / 1050
558 / 1050
559 / 1050
560 / 1050
561 / 1050
562 / 1050
563 / 1050
564 / 1050
565 / 1050
566 / 1050
567 / 1050
568 / 1050
569 / 1050
570 / 1050
571 / 1050
572 / 1050
573 / 1050
574 / 1050
575 / 1050
576 / 1050
577 / 1050
578 / 1050
579 / 1050
580 / 1050
581 / 1050
582 / 1050
583 / 1050
584 / 1050
585 / 1050
586 / 1050
587 / 1050
588 / 1050
589 / 1050
590 / 1050
591 / 1050
592 / 1050
593 / 1050
594 / 1050
595 / 1050
596 / 1050
597 / 1050
598 / 1050
599 / 1050
600 / 1050
601 / 1050
602 / 1050
603 / 1050
604 / 1050
605 / 1050
606 / 1050
607 / 1050
608 / 1050
609 / 1050
610 / 1050
611 / 1050
612 / 1050
613 / 1050
614 / 1050
615 / 1050
616 / 1050
617 / 1050
618 / 1050

174 / 661
175 / 661
176 / 661
177 / 661
178 / 661
179 / 661
180 / 661
181 / 661
182 / 661
183 / 661
184 / 661
185 / 661
186 / 661
187 / 661
188 / 661
189 / 661
190 / 661
191 / 661
192 / 661
193 / 661
194 / 661
195 / 661
196 / 661
197 / 661
198 / 661
199 / 661
200 / 661
201 / 661
202 / 661
203 / 661
204 / 661
205 / 661
206 / 661
207 / 661
208 / 661
209 / 661
210 / 661
211 / 661
212 / 661
213 / 661
214 / 661
215 / 661
216 / 661
217 / 661
218 / 661
219 / 661
220 / 661
221 / 661
222 / 661
223 / 661
224 / 661
225 / 661
226 / 661
227 / 661
228 / 661
229 / 661
230 / 661
231 / 661
232 / 661
233 / 661
234 / 661
235 / 661
236 / 661
237 / 661
238 / 661
239 / 661
240 / 661
241 / 661
242 / 661
243 / 661
244 / 661
245 / 661
246 / 661
247 / 661
248 / 661
249 / 661
250 / 661
251 / 661
252 / 661
253 / 661
254 / 661
255 / 661
256 / 661
257 / 661
258 / 661
259 / 661
260 / 661
261 / 661
262 / 661
263 / 661
264 / 661
265 / 661
266 / 661
267 / 661
268 / 661
269 / 661
270 / 661
271 / 661
272 / 661
273 / 661


239 / 543
240 / 543
241 / 543
242 / 543
243 / 543
244 / 543
245 / 543
246 / 543
247 / 543
248 / 543
249 / 543
250 / 543
251 / 543
252 / 543
253 / 543
254 / 543
255 / 543
256 / 543
257 / 543
258 / 543
259 / 543
260 / 543
261 / 543
262 / 543
263 / 543
264 / 543
265 / 543
266 / 543
267 / 543
268 / 543
269 / 543
270 / 543
271 / 543
272 / 543
273 / 543
274 / 543
275 / 543
276 / 543
277 / 543
278 / 543
279 / 543
280 / 543
281 / 543
282 / 543
283 / 543
284 / 543
285 / 543
286 / 543
287 / 543
288 / 543
289 / 543
290 / 543
291 / 543
292 / 543
293 / 543
294 / 543
295 / 543
296 / 543
297 / 543
298 / 543
299 / 543
300 / 543
301 / 543
302 / 543
303 / 543
304 / 543
305 / 543
306 / 543
307 / 543
308 / 543
309 / 543
310 / 543
311 / 543
312 / 543
313 / 543
314 / 543
315 / 543
316 / 543
317 / 543
318 / 543
319 / 543
320 / 543
321 / 543
322 / 543
323 / 543
324 / 543
325 / 543
326 / 543
327 / 543
328 / 543
329 / 543
330 / 543
331 / 543
332 / 543
333 / 543
334 / 543
335 / 543
336 / 543
337 / 543
338 / 543


297 / 435
298 / 435
299 / 435
300 / 435
301 / 435
302 / 435
303 / 435
304 / 435
305 / 435
306 / 435
307 / 435
308 / 435
309 / 435
310 / 435
311 / 435
312 / 435
313 / 435
314 / 435
315 / 435
316 / 435
317 / 435
318 / 435
319 / 435
320 / 435
321 / 435
322 / 435
323 / 435
324 / 435
325 / 435
326 / 435
327 / 435
328 / 435
329 / 435
330 / 435
331 / 435
332 / 435
333 / 435
334 / 435
335 / 435
336 / 435
337 / 435
338 / 435
339 / 435
340 / 435
341 / 435
342 / 435
343 / 435
344 / 435
345 / 435
346 / 435
347 / 435
348 / 435
349 / 435
350 / 435
351 / 435
352 / 435
353 / 435
354 / 435
355 / 435
356 / 435
357 / 435
358 / 435
359 / 435
360 / 435
361 / 435
362 / 435
363 / 435
364 / 435
365 / 435
366 / 435
367 / 435
368 / 435
369 / 435
370 / 435
371 / 435
372 / 435
373 / 435
374 / 435
375 / 435
376 / 435
377 / 435
378 / 435
379 / 435
380 / 435
381 / 435
382 / 435
383 / 435
384 / 435
385 / 435
386 / 435
387 / 435
388 / 435
389 / 435
390 / 435
391 / 435
392 / 435
393 / 435
394 / 435
395 / 435
396 / 435


69 / 87
70 / 87
71 / 87
72 / 87
73 / 87
74 / 87
75 / 87
76 / 87
77 / 87
78 / 87
79 / 87
80 / 87
81 / 87
82 / 87
83 / 87
84 / 87
85 / 87
86 / 87
87 / 87
Начало: mitsubishi | l400.
1 / 14
2 / 14
3 / 14
4 / 14
5 / 14
6 / 14
7 / 14
8 / 14
9 / 14
10 / 14
11 / 14
12 / 14
13 / 14
14 / 14
Начало: mitsubishi | mirage.
1 / 78
2 / 78
3 / 78
4 / 78
5 / 78
6 / 78
7 / 78
8 / 78
9 / 78
10 / 78
11 / 78
12 / 78
13 / 78
14 / 78
15 / 78
16 / 78
17 / 78
18 / 78
19 / 78
20 / 78
21 / 78
22 / 78
23 / 78
24 / 78
25 / 78
26 / 78
27 / 78
28 / 78
29 / 78
30 / 78
31 / 78
32 / 78
33 / 78
34 / 78
35 / 78
36 / 78
37 / 78
38 / 78
39 / 78
40 / 78
41 / 78
42 / 78
43 / 78
44 / 78
45 / 78
46 / 78
47 / 78
48 / 78
49 / 78
50 / 78
51 / 78
52 / 78
53 / 78
54 / 78
55 / 78
56 / 78
57 / 78
58 / 78
59 / 78
60 / 78
61 / 78
62 / 78
63 / 78
64 / 78
65 / 78
66 / 78
67 / 78
68 / 78
69 / 78
70 / 78
71 / 78
72 / 78
73 / 78
74 / 78
75 / 78
76 / 78
77 / 78
78 / 78
Начало: mitsubishi | dingo.
1 / 52
2 / 52
3 / 52
4 / 52
5 / 52
6 / 52
7 / 

In [12]:
#Чтение url-адресов в файл
with open('Data/dict_test_url.json', 'r') as f:
    dict_url_test = json.load(f)

In [15]:
#Перебор test
for brand in dict_url_test:
    print('Начало: {}.'.format(brand))
    mas = []
    l = len(dict_url_test[brand])
    for i, url in enumerate(dict_url_test[brand]):
        print('{} / {}'.format(i+1,l))
        response = requests.get(url)
        if response.status_code == 200:
            tree = html.fromstring(response.content)
            #Сбор данных
            xpath_date = tree.xpath('//div[contains(@title,"Дата")]//text()')
            mas += [[brand,url,xpath_date]]
    #Вывод в файл промежуточного результата
    pd.DataFrame(mas,columns=['brand','url','xpath_date']).to_csv('Data/test_date/test_'+brand+'.csv')

Начало: skoda.
1 / 2741
2 / 2741
3 / 2741
4 / 2741
5 / 2741
6 / 2741
7 / 2741
8 / 2741
9 / 2741
10 / 2741
11 / 2741
12 / 2741
13 / 2741
14 / 2741
15 / 2741
16 / 2741
17 / 2741
18 / 2741
19 / 2741
20 / 2741
21 / 2741
22 / 2741
23 / 2741
24 / 2741
25 / 2741
26 / 2741
27 / 2741
28 / 2741
29 / 2741
30 / 2741
31 / 2741
32 / 2741
33 / 2741
34 / 2741
35 / 2741
36 / 2741
37 / 2741
38 / 2741
39 / 2741
40 / 2741
41 / 2741
42 / 2741
43 / 2741
44 / 2741
45 / 2741
46 / 2741
47 / 2741
48 / 2741
49 / 2741
50 / 2741
51 / 2741
52 / 2741
53 / 2741
54 / 2741
55 / 2741
56 / 2741
57 / 2741
58 / 2741
59 / 2741
60 / 2741
61 / 2741
62 / 2741
63 / 2741
64 / 2741
65 / 2741
66 / 2741
67 / 2741
68 / 2741
69 / 2741
70 / 2741
71 / 2741
72 / 2741
73 / 2741
74 / 2741
75 / 2741
76 / 2741
77 / 2741
78 / 2741
79 / 2741
80 / 2741
81 / 2741
82 / 2741
83 / 2741
84 / 2741
85 / 2741
86 / 2741
87 / 2741
88 / 2741
89 / 2741
90 / 2741
91 / 2741
92 / 2741
93 / 2741
94 / 2741
95 / 2741
96 / 2741
97 / 2741
98 / 2741
99 / 2741
100 

755 / 2741
756 / 2741
757 / 2741
758 / 2741
759 / 2741
760 / 2741
761 / 2741
762 / 2741
763 / 2741
764 / 2741
765 / 2741
766 / 2741
767 / 2741
768 / 2741
769 / 2741
770 / 2741
771 / 2741
772 / 2741
773 / 2741
774 / 2741
775 / 2741
776 / 2741
777 / 2741
778 / 2741
779 / 2741
780 / 2741
781 / 2741
782 / 2741
783 / 2741
784 / 2741
785 / 2741
786 / 2741
787 / 2741
788 / 2741
789 / 2741
790 / 2741
791 / 2741
792 / 2741
793 / 2741
794 / 2741
795 / 2741
796 / 2741
797 / 2741
798 / 2741
799 / 2741
800 / 2741
801 / 2741
802 / 2741
803 / 2741
804 / 2741
805 / 2741
806 / 2741
807 / 2741
808 / 2741
809 / 2741
810 / 2741
811 / 2741
812 / 2741
813 / 2741
814 / 2741
815 / 2741
816 / 2741
817 / 2741
818 / 2741
819 / 2741
820 / 2741
821 / 2741
822 / 2741
823 / 2741
824 / 2741
825 / 2741
826 / 2741
827 / 2741
828 / 2741
829 / 2741
830 / 2741
831 / 2741
832 / 2741
833 / 2741
834 / 2741
835 / 2741
836 / 2741
837 / 2741
838 / 2741
839 / 2741
840 / 2741
841 / 2741
842 / 2741
843 / 2741
844 / 2741
845 / 2741

1459 / 2741
1460 / 2741
1461 / 2741
1462 / 2741
1463 / 2741
1464 / 2741
1465 / 2741
1466 / 2741
1467 / 2741
1468 / 2741
1469 / 2741
1470 / 2741
1471 / 2741
1472 / 2741
1473 / 2741
1474 / 2741
1475 / 2741
1476 / 2741
1477 / 2741
1478 / 2741
1479 / 2741
1480 / 2741
1481 / 2741
1482 / 2741
1483 / 2741
1484 / 2741
1485 / 2741
1486 / 2741
1487 / 2741
1488 / 2741
1489 / 2741
1490 / 2741
1491 / 2741
1492 / 2741
1493 / 2741
1494 / 2741
1495 / 2741
1496 / 2741
1497 / 2741
1498 / 2741
1499 / 2741
1500 / 2741
1501 / 2741
1502 / 2741
1503 / 2741
1504 / 2741
1505 / 2741
1506 / 2741
1507 / 2741
1508 / 2741
1509 / 2741
1510 / 2741
1511 / 2741
1512 / 2741
1513 / 2741
1514 / 2741
1515 / 2741
1516 / 2741
1517 / 2741
1518 / 2741
1519 / 2741
1520 / 2741
1521 / 2741
1522 / 2741
1523 / 2741
1524 / 2741
1525 / 2741
1526 / 2741
1527 / 2741
1528 / 2741
1529 / 2741
1530 / 2741
1531 / 2741
1532 / 2741
1533 / 2741
1534 / 2741
1535 / 2741
1536 / 2741
1537 / 2741
1538 / 2741
1539 / 2741
1540 / 2741
1541 / 2741
1542

2142 / 2741
2143 / 2741
2144 / 2741
2145 / 2741
2146 / 2741
2147 / 2741
2148 / 2741
2149 / 2741
2150 / 2741
2151 / 2741
2152 / 2741
2153 / 2741
2154 / 2741
2155 / 2741
2156 / 2741
2157 / 2741
2158 / 2741
2159 / 2741
2160 / 2741
2161 / 2741
2162 / 2741
2163 / 2741
2164 / 2741
2165 / 2741
2166 / 2741
2167 / 2741
2168 / 2741
2169 / 2741
2170 / 2741
2171 / 2741
2172 / 2741
2173 / 2741
2174 / 2741
2175 / 2741
2176 / 2741
2177 / 2741
2178 / 2741
2179 / 2741
2180 / 2741
2181 / 2741
2182 / 2741
2183 / 2741
2184 / 2741
2185 / 2741
2186 / 2741
2187 / 2741
2188 / 2741
2189 / 2741
2190 / 2741
2191 / 2741
2192 / 2741
2193 / 2741
2194 / 2741
2195 / 2741
2196 / 2741
2197 / 2741
2198 / 2741
2199 / 2741
2200 / 2741
2201 / 2741
2202 / 2741
2203 / 2741
2204 / 2741
2205 / 2741
2206 / 2741
2207 / 2741
2208 / 2741
2209 / 2741
2210 / 2741
2211 / 2741
2212 / 2741
2213 / 2741
2214 / 2741
2215 / 2741
2216 / 2741
2217 / 2741
2218 / 2741
2219 / 2741
2220 / 2741
2221 / 2741
2222 / 2741
2223 / 2741
2224 / 2741
2225

100 / 3421
101 / 3421
102 / 3421
103 / 3421
104 / 3421
105 / 3421
106 / 3421
107 / 3421
108 / 3421
109 / 3421
110 / 3421
111 / 3421
112 / 3421
113 / 3421
114 / 3421
115 / 3421
116 / 3421
117 / 3421
118 / 3421
119 / 3421
120 / 3421
121 / 3421
122 / 3421
123 / 3421
124 / 3421
125 / 3421
126 / 3421
127 / 3421
128 / 3421
129 / 3421
130 / 3421
131 / 3421
132 / 3421
133 / 3421
134 / 3421
135 / 3421
136 / 3421
137 / 3421
138 / 3421
139 / 3421
140 / 3421
141 / 3421
142 / 3421
143 / 3421
144 / 3421
145 / 3421
146 / 3421
147 / 3421
148 / 3421
149 / 3421
150 / 3421
151 / 3421
152 / 3421
153 / 3421
154 / 3421
155 / 3421
156 / 3421
157 / 3421
158 / 3421
159 / 3421
160 / 3421
161 / 3421
162 / 3421
163 / 3421
164 / 3421
165 / 3421
166 / 3421
167 / 3421
168 / 3421
169 / 3421
170 / 3421
171 / 3421
172 / 3421
173 / 3421
174 / 3421
175 / 3421
176 / 3421
177 / 3421
178 / 3421
179 / 3421
180 / 3421
181 / 3421
182 / 3421
183 / 3421
184 / 3421
185 / 3421
186 / 3421
187 / 3421
188 / 3421
189 / 3421
190 / 3421

...

18 / 2843
19 / 2843
20 / 2843
21 / 2843
22 / 2843
23 / 2843
24 / 2843
25 / 2843
26 / 2843
27 / 2843
28 / 2843
29 / 2843
30 / 2843
31 / 2843
32 / 2843
33 / 2843
34 / 2843
35 / 2843
36 / 2843
37 / 2843
38 / 2843
39 / 2843
40 / 2843
41 / 2843
42 / 2843
43 / 2843
44 / 2843
45 / 2843
46 / 2843
47 / 2843
48 / 2843
49 / 2843
50 / 2843
51 / 2843
52 / 2843
53 / 2843
54 / 2843
55 / 2843
56 / 2843
57 / 2843
58 / 2843
59 / 2843
60 / 2843
61 / 2843
62 / 2843
63 / 2843
64 / 2843
65 / 2843
66 / 2843
67 / 2843
68 / 2843
69 / 2843
70 / 2843
71 / 2843
72 / 2843
73 / 2843
74 / 2843
75 / 2843
76 / 2843
77 / 2843
78 / 2843
79 / 2843
80 / 2843
81 / 2843
82 / 2843
83 / 2843
84 / 2843
85 / 2843
86 / 2843
87 / 2843
88 / 2843
89 / 2843
90 / 2843
91 / 2843
92 / 2843
93 / 2843
94 / 2843
95 / 2843
96 / 2843
97 / 2843
98 / 2843
99 / 2843
100 / 2843
101 / 2843
102 / 2843
103 / 2843
104 / 2843
105 / 2843
106 / 2843
107 / 2843
108 / 2843
109 / 2843
110 / 2843
111 / 2843
112 / 2843
113 / 2843
114 / 2843
115 / 2843
116 

771 / 2843
772 / 2843
773 / 2843
774 / 2843
775 / 2843
776 / 2843
777 / 2843
778 / 2843
779 / 2843
780 / 2843
781 / 2843
782 / 2843
783 / 2843
784 / 2843
785 / 2843
786 / 2843
787 / 2843
788 / 2843
789 / 2843
790 / 2843
791 / 2843
792 / 2843
793 / 2843
794 / 2843
795 / 2843
796 / 2843
797 / 2843
798 / 2843
799 / 2843
800 / 2843
801 / 2843
802 / 2843
803 / 2843
804 / 2843
805 / 2843
806 / 2843
807 / 2843
808 / 2843
809 / 2843
810 / 2843
811 / 2843
812 / 2843
813 / 2843
814 / 2843
815 / 2843
816 / 2843
817 / 2843
818 / 2843
819 / 2843
820 / 2843
821 / 2843
822 / 2843
823 / 2843
824 / 2843
825 / 2843
826 / 2843
827 / 2843
828 / 2843
829 / 2843
830 / 2843
831 / 2843
832 / 2843
833 / 2843
834 / 2843
835 / 2843
836 / 2843
837 / 2843
838 / 2843
839 / 2843
840 / 2843
841 / 2843
842 / 2843
843 / 2843
844 / 2843
845 / 2843
846 / 2843
847 / 2843
848 / 2843
849 / 2843
850 / 2843
851 / 2843
852 / 2843
853 / 2843
854 / 2843
855 / 2843
856 / 2843
857 / 2843
858 / 2843
859 / 2843
860 / 2843
861 / 2843

1473 / 2843
1474 / 2843
1475 / 2843
1476 / 2843
1477 / 2843
1478 / 2843
1479 / 2843
1480 / 2843
1481 / 2843
1482 / 2843
1483 / 2843
1484 / 2843
1485 / 2843
1486 / 2843
1487 / 2843
1488 / 2843
1489 / 2843
1490 / 2843
1491 / 2843
1492 / 2843
1493 / 2843
1494 / 2843
1495 / 2843
1496 / 2843
1497 / 2843
1498 / 2843
1499 / 2843
1500 / 2843
1501 / 2843
1502 / 2843
1503 / 2843
1504 / 2843
1505 / 2843
1506 / 2843
1507 / 2843
1508 / 2843
1509 / 2843
1510 / 2843
1511 / 2843
1512 / 2843
1513 / 2843
1514 / 2843
1515 / 2843
1516 / 2843
1517 / 2843
1518 / 2843
1519 / 2843
1520 / 2843
1521 / 2843
1522 / 2843
1523 / 2843
1524 / 2843
1525 / 2843
1526 / 2843
1527 / 2843
1528 / 2843
1529 / 2843
1530 / 2843
1531 / 2843
1532 / 2843
1533 / 2843
1534 / 2843
1535 / 2843
1536 / 2843
1537 / 2843
1538 / 2843
1539 / 2843
1540 / 2843
1541 / 2843
1542 / 2843
1543 / 2843
1544 / 2843
1545 / 2843
1546 / 2843
1547 / 2843
1548 / 2843
1549 / 2843
1550 / 2843
1551 / 2843
1552 / 2843
1553 / 2843
1554 / 2843
1555 / 2843
1556

2156 / 2843
2157 / 2843
2158 / 2843
2159 / 2843
2160 / 2843
2161 / 2843
2162 / 2843
2163 / 2843
2164 / 2843
2165 / 2843
2166 / 2843
2167 / 2843
2168 / 2843
2169 / 2843
2170 / 2843
2171 / 2843
2172 / 2843
2173 / 2843
2174 / 2843
2175 / 2843
2176 / 2843
2177 / 2843
2178 / 2843
2179 / 2843
2180 / 2843
2181 / 2843
2182 / 2843
2183 / 2843
2184 / 2843
2185 / 2843
2186 / 2843
2187 / 2843
2188 / 2843
2189 / 2843
2190 / 2843
2191 / 2843
2192 / 2843
2193 / 2843
2194 / 2843
2195 / 2843
2196 / 2843
2197 / 2843
2198 / 2843
2199 / 2843
2200 / 2843
2201 / 2843
2202 / 2843
2203 / 2843
2204 / 2843
2205 / 2843
2206 / 2843
2207 / 2843
2208 / 2843
2209 / 2843
2210 / 2843
2211 / 2843
2212 / 2843
2213 / 2843
2214 / 2843
2215 / 2843
2216 / 2843
2217 / 2843
2218 / 2843
2219 / 2843
2220 / 2843
2221 / 2843
2222 / 2843
2223 / 2843
2224 / 2843
2225 / 2843
2226 / 2843
2227 / 2843
2228 / 2843
2229 / 2843
2230 / 2843
2231 / 2843
2232 / 2843
2233 / 2843
2234 / 2843
2235 / 2843
2236 / 2843
2237 / 2843
2238 / 2843
2239

2839 / 2843
2840 / 2843
2841 / 2843
2842 / 2843
2843 / 2843
